In [1]:
 # Install the OpenSlide C library and Python bindings
!apt-get install openslide-tools
!pip install openslide-python

/bin/sh: apt-get: command not found
DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that date. A future version of pip will drop support for Python 2.7.
  Using cached https://files.pythonhosted.org/packages/26/5a/5b0adeabce81f018a9e4ffe9a419536064bc95c1b12194aff9b7e48f91f7/openslide-python-1.1.1.tar.gz
  Stored in directory: /Users/sujipark/Library/Caches/pip/wheels/56/44/7e/16c9fc72cfbf1bffe48676b6835843d21abcc56566e958e7d6
Successfully built openslide-python


In [2]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from openslide import open_slide, __library_version__ as openslide_version
import os
from PIL import Image
from skimage.color import rgb2gray

In [3]:
mypath = "/Users/sujipark/documents/slides"

In [4]:
!pip install opencv-python

DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that date. A future version of pip will drop support for Python 2.7.
    100% |████████████████████████████████| 52.1MB 304kB/s eta 0:00:01


#Processing Data





## Splitting Slides into Train/Validation/Testing

In [5]:
from os import listdir
from os.path import isfile, join
import os.path

images = []

onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]
for fn in onlyfiles:
  if (os.path.splitext(fn)[0] not in images) and ('mask' not in os.path.splitext(fn)[0]):
    images.append(os.path.splitext(fn)[0])

# remove unusual tumor images
images.remove("tumor_038")
images.remove("tumor_038(1)")
images.remove("tumor_099")
images.remove('.DS_Store')
images.remove('tumor_001-017')
print(images)


['tumor_016', 'tumor_002', 'tumor_064', 'tumor_110', 'tumor_001', 'tumor_059', 'tumor_075', 'tumor_005', 'tumor_101', 'tumor_012', 'tumor_019', 'tumor_031', 'tumor_096', 'tumor_081', 'tumor_094', 'tumor_057', 'tumor_023', 'tumor_084', 'tumor_091', 'tumor_078', 'tumor_035']


In [6]:
print("Number of slides: %d" %(len(images)))

Number of slides: 21


In [7]:
import random 

random.seed(1)
random.shuffle(images)

train_data = images[:17]
val_data = images[17:21]
print("#train: %d, #validation: %d" %(len(train_data), len(val_data)))

#train: 17, #validation: 4


In [8]:
print(train_data)
print(val_data)

['tumor_059', 'tumor_057', 'tumor_035', 'tumor_078', 'tumor_096', 'tumor_019', 'tumor_110', 'tumor_081', 'tumor_075', 'tumor_084', 'tumor_091', 'tumor_016', 'tumor_002', 'tumor_031', 'tumor_012', 'tumor_005', 'tumor_101']
['tumor_001', 'tumor_094', 'tumor_023', 'tumor_064']


In [9]:
# create directories
!rm -rf data/

import os 
def create_level_dir(dir_name):
  z5_dir = os.path.join(dir_name, 'z5')
  z4_dir = os.path.join(dir_name, 'z4')
  z3_dir = os.path.join(dir_name, 'z3')
  z2_dir = os.path.join(dir_name, 'z2')
  z1_dir = os.path.join(dir_name, 'z1')
  z0_dir = os.path.join(dir_name, 'z0')

  os.mkdir(z0_dir)
  os.mkdir(z1_dir)
  os.mkdir(z2_dir)
  os.mkdir(z3_dir)
  os.mkdir(z4_dir)
  os.mkdir(z5_dir)

  return z0_dir, z1_dir, z2_dir, z3_dir, z4_dir, z5_dir
  
def label_directory(dir_name):
  z0_dir, z1_dir, z2_dir, z3_dir, z4_dir, z5_dir = create_level_dir(dir_name)
  os.mkdir(os.path.join(z0_dir, 'tumor'))
  os.mkdir(os.path.join(z0_dir, 'no_tumor'))
  os.mkdir(os.path.join(z1_dir, 'tumor'))
  os.mkdir(os.path.join(z1_dir, 'no_tumor'))
  os.mkdir(os.path.join(z2_dir, 'tumor'))
  os.mkdir(os.path.join(z2_dir, 'no_tumor'))
  os.mkdir(os.path.join(z3_dir, 'tumor'))
  os.mkdir(os.path.join(z3_dir, 'no_tumor'))
  os.mkdir(os.path.join(z4_dir, 'tumor'))
  os.mkdir(os.path.join(z4_dir, 'no_tumor'))
  os.mkdir(os.path.join(z5_dir, 'tumor'))
  os.mkdir(os.path.join(z5_dir, 'no_tumor'))

base_dir = 'data/'
train_dir = os.path.join(base_dir, 'train')
val_dir =  os.path.join(base_dir, 'val') 

if not os.path.exists(base_dir):
  os.mkdir(base_dir)
  
if not os.path.exists(train_dir):
  os.mkdir(train_dir)
  label_directory(train_dir)

if not os.path.exists(val_dir):
  os.mkdir(val_dir)
  label_directory(val_dir)
  
print('train_dir: %s, val_dir: %s ' %(train_dir, val_dir))

train_dir: data/train, val_dir: data/val 


## Classifying the Data by Labels

In [10]:
def read_slide(slide, x, y, level, width, height, as_float=False, mask=False):
    im = slide.read_region((x,y), level, (width, height))
    im = im.convert('RGB') # drop the alpha channel
    if as_float:
        im = np.asarray(im, dtype=np.float32)
    else:
        im = np.asarray(im)
    assert im.shape == (height, width, 3)
    return (im if not mask else im[:, :, 0])

# overlaying a mask over image
def apply_mask(im, mask):
    masked =np.zeros_like(im)
    for x,y in mask: 
      masked[x][y] = 1
    return masked
  
# search for grey regions
def find_tissue_pixels(image, intensity=0.8):
    im_gray = rgb2gray(image)
    assert im_gray.shape == (image.shape[0], image.shape[1])
    indices = np.where(im_gray <= intensity)
    return zip(indices[0], indices[1])

In [11]:
import math
import cv2
def preprocess(im_name, level, is_train = False, is_val = False):
  # Process images of lower zoom level, which have memory issues if try to process whole slice
  slide_path = os.path.join(mypath, im_name)+ ".tif"
  mask_path = os.path.join(mypath, im_name) + "_mask.tif"
  slide = open_slide(slide_path)
  tumor_mask = open_slide(mask_path)
  x_dim = (slide.level_dimensions[level][0]) #15360
  y_dim = (slide.level_dimensions[level][1]) #13440
  
  x_num= int(math.ceil(x_dim/ 299))
  y_num = int(math.ceil(y_dim/299))
  idx = 0
  for i in range(x_num):
    lower_x = i*299 * (2**level)
    for j in range(y_num):
      lower_y = j * 299 *(2**level)
      img_window = read_slide(slide, 
                     x=lower_x, 
                     y=lower_y, 
                     level=level, 
                     width=299, 
                     height=299)
      mask_window = read_slide(tumor_mask, 
                     x=lower_x, 
                     y=lower_y, 
                     level=level, 
                     width=299, 
                     height=299,
                     mask = True)

      tissue_pixels = find_tissue_pixels(img_window)
      percent_tissue = len(tissue_pixels) / float(img_window.shape[0] * img_window.shape[0])
      tissue_region = apply_mask(img_window, tissue_pixels)
      tissue_threshold = .3
      if is_train:
        dir_route = 'train'
      if is_val:
        dir_route = 'val'
      if percent_tissue> tissue_threshold:
        img_fn = 'level_'+str(level)+'_' + im_name +"_"+ str(idx)
        if np.max(mask_window) > 0:
          img_output_fn = "data/" + dir_route + "/z" + str(level)+"/tumor/" + img_fn + ".jpg" 
        else:
          img_output_fn= "data/"+ dir_route + "/z" + str(level)+"/no_tumor/" + img_fn + ".jpg"
        print(img_output_fn)
        cv2.imwrite(img_output_fn, img_window)
      idx = idx+1

In [14]:
# levels = [5, 4, 3, 2]
levels = [1]


for level in levels:
  for val_fn in train_data:
    preprocess(val_fn, level, is_train = True)
  print("Done with zoom %d" %level)
  
for level in levels:
  for val_fn in val_data:
    preprocess(val_fn, level, is_val = True)
  print("Done with zoom %d" %level)


data/train/z1/no_tumor/level_1_tumor_059_1.jpg
data/train/z1/no_tumor/level_1_tumor_059_2.jpg
data/train/z1/no_tumor/level_1_tumor_059_3.jpg
data/train/z1/no_tumor/level_1_tumor_059_370.jpg
data/train/z1/no_tumor/level_1_tumor_059_371.jpg
data/train/z1/no_tumor/level_1_tumor_059_372.jpg
data/train/z1/no_tumor/level_1_tumor_059_531.jpg
data/train/z1/no_tumor/level_1_tumor_059_533.jpg
data/train/z1/no_tumor/level_1_tumor_059_534.jpg
data/train/z1/no_tumor/level_1_tumor_059_535.jpg
data/train/z1/no_tumor/level_1_tumor_059_536.jpg
data/train/z1/no_tumor/level_1_tumor_059_537.jpg
data/train/z1/no_tumor/level_1_tumor_059_538.jpg
data/train/z1/no_tumor/level_1_tumor_059_539.jpg
data/train/z1/no_tumor/level_1_tumor_059_540.jpg
data/train/z1/no_tumor/level_1_tumor_059_541.jpg
data/train/z1/no_tumor/level_1_tumor_059_542.jpg
data/train/z1/no_tumor/level_1_tumor_059_543.jpg
data/train/z1/no_tumor/level_1_tumor_059_544.jpg
data/train/z1/no_tumor/level_1_tumor_059_545.jpg
data/train/z1/no_tumor/lev

data/train/z1/no_tumor/level_1_tumor_059_898.jpg
data/train/z1/no_tumor/level_1_tumor_059_899.jpg
data/train/z1/no_tumor/level_1_tumor_059_900.jpg
data/train/z1/no_tumor/level_1_tumor_059_901.jpg
data/train/z1/no_tumor/level_1_tumor_059_902.jpg
data/train/z1/no_tumor/level_1_tumor_059_903.jpg
data/train/z1/no_tumor/level_1_tumor_059_904.jpg
data/train/z1/no_tumor/level_1_tumor_059_1108.jpg
data/train/z1/no_tumor/level_1_tumor_059_1109.jpg
data/train/z1/no_tumor/level_1_tumor_059_1110.jpg
data/train/z1/no_tumor/level_1_tumor_059_1135.jpg
data/train/z1/no_tumor/level_1_tumor_059_1136.jpg
data/train/z1/no_tumor/level_1_tumor_059_1137.jpg
data/train/z1/no_tumor/level_1_tumor_059_1138.jpg
data/train/z1/no_tumor/level_1_tumor_059_1139.jpg
data/train/z1/no_tumor/level_1_tumor_059_1140.jpg
data/train/z1/no_tumor/level_1_tumor_059_1141.jpg
data/train/z1/no_tumor/level_1_tumor_059_1142.jpg
data/train/z1/no_tumor/level_1_tumor_059_1143.jpg
data/train/z1/no_tumor/level_1_tumor_059_1144.jpg
data/tr

data/train/z1/no_tumor/level_1_tumor_059_8513.jpg
data/train/z1/no_tumor/level_1_tumor_059_8514.jpg
data/train/z1/no_tumor/level_1_tumor_059_8515.jpg
data/train/z1/no_tumor/level_1_tumor_059_8516.jpg
data/train/z1/no_tumor/level_1_tumor_059_8517.jpg
data/train/z1/no_tumor/level_1_tumor_059_8518.jpg
data/train/z1/no_tumor/level_1_tumor_059_8519.jpg
data/train/z1/no_tumor/level_1_tumor_059_8520.jpg
data/train/z1/no_tumor/level_1_tumor_059_8857.jpg
data/train/z1/no_tumor/level_1_tumor_059_8858.jpg
data/train/z1/no_tumor/level_1_tumor_059_8859.jpg
data/train/z1/no_tumor/level_1_tumor_059_8875.jpg
data/train/z1/no_tumor/level_1_tumor_059_8876.jpg
data/train/z1/no_tumor/level_1_tumor_059_8877.jpg
data/train/z1/no_tumor/level_1_tumor_059_8878.jpg
data/train/z1/no_tumor/level_1_tumor_059_8879.jpg
data/train/z1/no_tumor/level_1_tumor_059_8880.jpg
data/train/z1/no_tumor/level_1_tumor_059_8881.jpg
data/train/z1/no_tumor/level_1_tumor_059_8882.jpg
data/train/z1/no_tumor/level_1_tumor_059_8883.jpg


data/train/z1/no_tumor/level_1_tumor_059_15870.jpg
data/train/z1/no_tumor/level_1_tumor_059_15895.jpg
data/train/z1/no_tumor/level_1_tumor_059_16039.jpg
data/train/z1/no_tumor/level_1_tumor_059_16044.jpg
data/train/z1/no_tumor/level_1_tumor_059_16045.jpg
data/train/z1/no_tumor/level_1_tumor_059_16046.jpg
data/train/z1/no_tumor/level_1_tumor_059_16047.jpg
data/train/z1/no_tumor/level_1_tumor_059_16048.jpg
data/train/z1/no_tumor/level_1_tumor_059_16049.jpg
data/train/z1/no_tumor/level_1_tumor_059_16050.jpg
data/train/z1/no_tumor/level_1_tumor_059_16236.jpg
data/train/z1/no_tumor/level_1_tumor_059_16237.jpg
data/train/z1/no_tumor/level_1_tumor_059_16238.jpg
data/train/z1/no_tumor/level_1_tumor_059_16239.jpg
data/train/z1/no_tumor/level_1_tumor_059_16264.jpg
data/train/z1/no_tumor/level_1_tumor_059_16411.jpg
data/train/z1/no_tumor/level_1_tumor_059_16414.jpg
data/train/z1/no_tumor/level_1_tumor_059_16415.jpg
data/train/z1/no_tumor/level_1_tumor_059_16416.jpg
data/train/z1/no_tumor/level_1_

data/train/z1/no_tumor/level_1_tumor_059_21247.jpg
data/train/z1/no_tumor/level_1_tumor_059_21248.jpg
data/train/z1/no_tumor/level_1_tumor_059_21249.jpg
data/train/z1/no_tumor/level_1_tumor_059_21250.jpg
data/train/z1/no_tumor/level_1_tumor_059_21251.jpg
data/train/z1/no_tumor/level_1_tumor_059_21252.jpg
data/train/z1/no_tumor/level_1_tumor_059_21253.jpg
data/train/z1/no_tumor/level_1_tumor_059_21256.jpg
data/train/z1/no_tumor/level_1_tumor_059_21257.jpg
data/train/z1/no_tumor/level_1_tumor_059_21258.jpg
data/train/z1/no_tumor/level_1_tumor_059_21259.jpg
data/train/z1/no_tumor/level_1_tumor_059_21260.jpg
data/train/z1/no_tumor/level_1_tumor_059_21263.jpg
data/train/z1/no_tumor/level_1_tumor_059_21402.jpg
data/train/z1/no_tumor/level_1_tumor_059_21403.jpg
data/train/z1/no_tumor/level_1_tumor_059_21404.jpg
data/train/z1/no_tumor/level_1_tumor_059_21405.jpg
data/train/z1/no_tumor/level_1_tumor_059_21430.jpg
data/train/z1/no_tumor/level_1_tumor_059_21612.jpg
data/train/z1/no_tumor/level_1_

...

data/val/z1/no_tumor/level_1_tumor_064_44646.jpg
data/val/z1/no_tumor/level_1_tumor_064_44677.jpg
data/val/z1/no_tumor/level_1_tumor_064_44873.jpg
data/val/z1/no_tumor/level_1_tumor_064_44874.jpg
data/val/z1/no_tumor/level_1_tumor_064_44875.jpg
data/val/z1/no_tumor/level_1_tumor_064_44876.jpg
data/val/z1/no_tumor/level_1_tumor_064_44877.jpg
data/val/z1/no_tumor/level_1_tumor_064_44878.jpg
data/val/z1/no_tumor/level_1_tumor_064_44879.jpg
data/val/z1/no_tumor/level_1_tumor_064_44880.jpg
data/val/z1/no_tumor/level_1_tumor_064_44881.jpg
data/val/z1/no_tumor/level_1_tumor_064_44882.jpg
data/val/z1/no_tumor/level_1_tumor_064_44883.jpg
data/val/z1/no_tumor/level_1_tumor_064_44884.jpg
data/val/z1/no_tumor/level_1_tumor_064_44885.jpg
data/val/z1/no_tumor/level_1_tumor_064_44886.jpg
data/val/z1/no_tumor/level_1_tumor_064_44887.jpg
data/val/z1/no_tumor/level_1_tumor_064_44888.jpg
data/val/z1/no_tumor/level_1_tumor_064_44889.jpg
data/val/z1/no_tumor/level_1_tumor_064_44890.jpg
data/val/z1/no_tumor

data/val/z1/no_tumor/level_1_tumor_064_47092.jpg
data/val/z1/no_tumor/level_1_tumor_064_47093.jpg
data/val/z1/no_tumor/level_1_tumor_064_47094.jpg
data/val/z1/no_tumor/level_1_tumor_064_47095.jpg
data/val/z1/no_tumor/level_1_tumor_064_47096.jpg
data/val/z1/no_tumor/level_1_tumor_064_47097.jpg
data/val/z1/no_tumor/level_1_tumor_064_47098.jpg
data/val/z1/no_tumor/level_1_tumor_064_47099.jpg
data/val/z1/no_tumor/level_1_tumor_064_47101.jpg
data/val/z1/no_tumor/level_1_tumor_064_47102.jpg
data/val/z1/no_tumor/level_1_tumor_064_47103.jpg
data/val/z1/no_tumor/level_1_tumor_064_47104.jpg
data/val/z1/no_tumor/level_1_tumor_064_47126.jpg
data/val/z1/no_tumor/level_1_tumor_064_47260.jpg
data/val/z1/no_tumor/level_1_tumor_064_47455.jpg
data/val/z1/no_tumor/level_1_tumor_064_47456.jpg
data/val/z1/no_tumor/level_1_tumor_064_47457.jpg
data/val/z1/no_tumor/level_1_tumor_064_47458.jpg
data/val/z1/no_tumor/level_1_tumor_064_47459.jpg
data/val/z1/no_tumor/level_1_tumor_064_47460.jpg
data/val/z1/no_tumor

data/val/z1/no_tumor/level_1_tumor_064_49695.jpg
data/val/z1/no_tumor/level_1_tumor_064_49696.jpg
data/val/z1/no_tumor/level_1_tumor_064_49697.jpg
data/val/z1/no_tumor/level_1_tumor_064_49698.jpg
data/val/z1/no_tumor/level_1_tumor_064_49699.jpg
data/val/z1/no_tumor/level_1_tumor_064_49700.jpg
data/val/z1/no_tumor/level_1_tumor_064_49701.jpg
data/val/z1/no_tumor/level_1_tumor_064_49702.jpg
data/val/z1/no_tumor/level_1_tumor_064_49703.jpg
data/val/z1/no_tumor/level_1_tumor_064_49704.jpg
data/val/z1/no_tumor/level_1_tumor_064_49705.jpg
data/val/z1/no_tumor/level_1_tumor_064_49706.jpg
data/val/z1/no_tumor/level_1_tumor_064_49843.jpg
data/val/z1/no_tumor/level_1_tumor_064_50039.jpg
data/val/z1/no_tumor/level_1_tumor_064_50040.jpg
data/val/z1/no_tumor/level_1_tumor_064_50041.jpg
data/val/z1/no_tumor/level_1_tumor_064_50042.jpg
data/val/z1/no_tumor/level_1_tumor_064_50043.jpg
data/val/z1/no_tumor/level_1_tumor_064_50044.jpg
data/val/z1/no_tumor/level_1_tumor_064_50045.jpg
data/val/z1/no_tumor

data/val/z1/tumor/level_1_tumor_064_51529.jpg
data/val/z1/tumor/level_1_tumor_064_51530.jpg
data/val/z1/tumor/level_1_tumor_064_51531.jpg
data/val/z1/tumor/level_1_tumor_064_51532.jpg
data/val/z1/tumor/level_1_tumor_064_51533.jpg
data/val/z1/no_tumor/level_1_tumor_064_51534.jpg
data/val/z1/no_tumor/level_1_tumor_064_51535.jpg
data/val/z1/no_tumor/level_1_tumor_064_51536.jpg
data/val/z1/no_tumor/level_1_tumor_064_51537.jpg
data/val/z1/no_tumor/level_1_tumor_064_51538.jpg
data/val/z1/no_tumor/level_1_tumor_064_51539.jpg
data/val/z1/no_tumor/level_1_tumor_064_51540.jpg
data/val/z1/no_tumor/level_1_tumor_064_51541.jpg
data/val/z1/no_tumor/level_1_tumor_064_51542.jpg
data/val/z1/no_tumor/level_1_tumor_064_51543.jpg
data/val/z1/no_tumor/level_1_tumor_064_51544.jpg
data/val/z1/no_tumor/level_1_tumor_064_51545.jpg
data/val/z1/no_tumor/level_1_tumor_064_51546.jpg
data/val/z1/no_tumor/level_1_tumor_064_51547.jpg
data/val/z1/no_tumor/level_1_tumor_064_51657.jpg
data/val/z1/no_tumor/level_1_tumor_

data/val/z1/no_tumor/level_1_tumor_064_53734.jpg
data/val/z1/no_tumor/level_1_tumor_064_53735.jpg
data/val/z1/no_tumor/level_1_tumor_064_53736.jpg
data/val/z1/no_tumor/level_1_tumor_064_53737.jpg
data/val/z1/no_tumor/level_1_tumor_064_53738.jpg
data/val/z1/no_tumor/level_1_tumor_064_53739.jpg
data/val/z1/no_tumor/level_1_tumor_064_53740.jpg
data/val/z1/no_tumor/level_1_tumor_064_53741.jpg
data/val/z1/no_tumor/level_1_tumor_064_53742.jpg
data/val/z1/no_tumor/level_1_tumor_064_53743.jpg
data/val/z1/no_tumor/level_1_tumor_064_53744.jpg
data/val/z1/no_tumor/level_1_tumor_064_53745.jpg
data/val/z1/no_tumor/level_1_tumor_064_53746.jpg
data/val/z1/no_tumor/level_1_tumor_064_53747.jpg
data/val/z1/no_tumor/level_1_tumor_064_53748.jpg
data/val/z1/no_tumor/level_1_tumor_064_53749.jpg
data/val/z1/no_tumor/level_1_tumor_064_53750.jpg
data/val/z1/no_tumor/level_1_tumor_064_53751.jpg
data/val/z1/no_tumor/level_1_tumor_064_53752.jpg
data/val/z1/no_tumor/level_1_tumor_064_53753.jpg
data/val/z1/no_tumor

## Count of Train/Test/Val Images

In [3]:
!find data/train/z1/tumor -type f | wc -l
!find data/train/z1/no_tumor -type f | wc -l


!find data/val/z1/tumor -type f | wc -l
!find data/val/z1/no_tumor -type f | wc -l

    9780
   56389
     749
   17337
